# Smoothed-particle hydrodynamics

We have just seen that that we can use continuum equation to capture the bulk motion of particles when the number of collisions is large enough to force particles to move randomly.  This randomness effectively sample the whole phase space in such a way that particle distribution relaxes into Gaussian distributions. We call this behavior *collisional*.



However, there are some case when this is not the case. And we have seen an example in the previous chapter, captured by particle-in-cell codes. In this case, the particles are *kinetic*, as there is not enough collisions to smooth out the distribution function. They  obviously still conserve mass, moment and energy microscopically. However, their behavior precludes to track exchanges of macroscopic scales. As a result, the macroscopic conservation laws do not apply. In a nutshell, Eq. $(4.11)$, $(4.17)$ and $(4.21)$ cannot be derived simply by integrating the Boltzmann equation.


An example can be easily devised. Take a particle that is accelerated by an electric field. At the beginning it will collide with other particles. But, if the collisions are not enough to turn the average acceleration to 0, the particle will slowly accelerate. Since the collision frequency goes as $v^{-3}$, collisions will be less frequent. There will be a point where the particle will carry its mass, momentum and energy across long distances without collisions. When it will collide, it will share momentum and energy with another particle. 

By taking energy and momentum from a location in space and dropping into another region which are seemingly not connected, this particle will make momentum and energy appear *magically* at this location. This would clearly violate the macroscopic conservation laws (energy and momentum would not be conserved). Yet the whole system did conserve mass, momentum and energy. So no physics laws are violated microscopically. This means the system is kinetic and cannot be capture by smoothing the particle distribution function.

But there is actually a world in between. In this world, particles are overall following macroscopic conservation laws, but there is a kinetic component that cannot be ignored. This is where smooth particle hydrodynamics comes in. As you saw in the PIC code, we deposited charges on a grid to compute the field there and avoid the $N^2$ dependence we would get if we were to look at binary interaction between $N$ particles.

Smooth particle hydrodynamics drops the grid and compute binary interactions. But it is done by only looking *locally* around each particles. So if we suppose that each particle interact with at most $P$ particle, where $P<<N$ then we have a computational complexity which is proportinal to $N$ instead of $N^2$.

As we did in the PIC code, we start with a collection of particle clumps (or meta-particle). But, rather supposing this clump to be small (spanning only a few grid cells in the PIC code), we gonna suppose this clump to be really wide. We will only track its center gravity and its breadth will be represented by a shape function, or kernel. But this *smoothing* function cannot be random. It needs to have properties that makes it easy to handle numerically. 

Typically we will use a [radial basis function](https://arxiv.org/pdf/0909.5413.pdf), because it forms linear systems that can be inverted easily to find solutions. Regardless of the reason, these properties allow the algorithms to be stable. One example is the Gaussian function, used earlier in this chapter. We will use here functions that are easier to compute and, unlike Gaussians, are compact (meaning they reach 0 at some point) while Gaussians only reach 0 at $\infty$.

Radial basis functions are defined by distance rather than location in space, i.e. for $x\in \mathbb{R}^d$ we have $\Phi(x)=\phi(||x||_d)$. With no loss in generality we can define $\Phi(0)=1$. We can generate new functions by translating this function using a point $x_0\in \mathbb{R}^d$ by simply writing $\Phi_{x_0}(x)=\phi(||x-x_0||_d)$, which will also write as $\Phi(x-x_0)$. We can also scale the function $\Phi_{x_0}$ by a factor $\alpha$ as such, $\Phi_{\alpha, x_0}(x)=\phi(||x-x_0||_d/\alpha)$, which will also write as $\Phi_{\alpha}(x-x_0)$. Because $\Phi_{\alpha,x_0}$ is just a scaled, translate version of $\phi$, we call the function $\phi(r),\forall r\in \mathbb R$ the mother radial basis function.

Here is a list of radial basis functions:

Gaussian : $\phi(r/\alpha)=e^{-r^2/\alpha^2}$<br>
Multiquadric : $\phi(r/\alpha)=\sqrt{1+r^2/\alpha^2}$<br>
Inverse Quadric : $\phi(r/\alpha)=\frac{1}{\sqrt{1+r^2/\alpha^2}}$<br>
Wendland compactly supported: $\phi(r/\alpha)=(1-\frac{r}{\alpha})^4(1+4\frac{r}{\alpha})$ only if $r<\alpha$, $0$ otherwise

Note that the Wendland function is one of many. This one is definite positive and $C^2$ in $\mathbb R^3$ so its first derivative is continuous. We will use this one is the rest of the notebook.

### Compute and share
Share with the audience what you find when

1. you plot the for different functions on a graph to see the difference between each functions
2. add a scaling factor $\alpha$ and show how it modifies one function

### The governing equations
Going back to the PIC, particles will feel forces. But, unlike in PIC codes, the force will be computed via truncated binary interactions. The truncation will take place where the radius $r_{ij}=||\vec x_i-\vec x_j||$ between two meta-particles $i$ and $j$ is larger than $\alpha$. This way of coupling particles together, via their kernel interaction, is called *smooth particle hydrodynamics* or SPH.

This approach conserves mass by default, and momentum and energy if the algorithm is properly designed. So, there is no need to use a kinetic version of the macroscopic version of the conservation laws previously described. We only need to compute the trajectory of meta-particle that interact with their own kernels.

In its simplest form, the trajectory is described by Newton's second law: $$\rho\frac{d\vec v}{dt}=-\vec\nabla P+\vec f\tag{4.27}$$ Here $\rho$ is the *mass density* (not the charge density), $\vec v$ is the particle velocity, $P$ is the pressure (i.e. energy density since $Pa$ is $Jm^{-3}$) and $\vec f$ is a force density.

In [ ]:
class particle:
    m=1.6726219e-27 #mass
    rho=0 #density
    P=0 #pressure
    x=0 #location
    v=0 #speed

At this point we face two basic problems. First, how to define local, intensive quantities (like $\rho$ or $P$) and how to define derivatives (hidden in the $\vec\nabla$ operator).

If we suppose that each meta particle $i$ has a mass $m_i$, we can define $\rho_i$ as $$\rho_i=\sum_j m_j W_{\alpha,x_j}(\vec x_i)=\sum_j m_j W_{\alpha}(\vec x_i-\vec x_j)\tag{4.28}$$ where $W_{\alpha,x_j}$ is the radial function $\Phi_{\alpha,x_j}$, centered on $\vec x_j$ and scaled by $\alpha$ and that has been normalized across our domain $\Omega$ in such a way as $\int_\Omega W_{\alpha,x_j}(\vec x)d\vec x=1$. *Note that the tiny subscipt next to $W$ is $\alpha$ not $a$.*

In [ ]:
def compute_rho(particles):
    global alpha
    for i in range (len(particles)):
        particles[i].rho=0
        for j in range(len(particles)):
            r=particles[i].x-particles[j].x
            r=(r[0]**2+r[1]**2+r[2]**2)**.5
            particles[i].rho+=W(r,alpha)*particles[j].m

We can form $W_{\alpha,x_j}$ easily as $$W_{\alpha,x_j}=\frac{1}{\alpha^3\int_{0}^{+\infty}4\pi r^2\phi(r)dr}\Phi_{\alpha,x_j}$$Note that $\alpha^3$ and $4\pi r^2$ are there because we work in three dimensions. In two dimensions replace $\alpha^3$ by $\alpha^2$ and $4\pi r^2$ by $2\pi r$. Also note that $W_{\alpha,x_j}$ has a unit which is the same as $1/\alpha^3$. So it is in $m^{-3}$.

In [ ]:
def W(ri,alpha=1): 
    r=abs(ri/alpha)    
    y=0
    if (r<=1):
        y=21./2./np.pi*(1-r)**4*(1+4*r)
    return y/alpha**3

In [ ]:
def dW(ri,alpha=1):
    r=abs(ri/alpha)
    y=0
    if (r<=1):
        y=210./np.pi*(r-1)**3*r
    return y/alpha**4

Based on this definition, we see that the total mass $M$ of the system $$M=\int_{\Omega}\rho d\vec x=\sum_j m_j$$

So, how do we define $P$ ? <br>$P$ is the pressure and it relates to the mass density and the temperature via an *equation of state*. The most famous one is the ideal gas equation of state, $P=neT$, where the temperature $T$ is in $V$. 

We won't be using this equation to keep our problem simple. So let's get rid of $T$ and use the equation of state $PV^{\gamma}$ is constant, leading to the polytropic equation $$P=K\rho^{\gamma}\tag{4.29}$$

In [ ]:
def compute_pressure(particles,K=1,aindex=1.5):
    for i in range (len(particles)):
        particles[i].P=K*particles[i].rho**aindex

We are now done with our two state variables. Let's look at how SPH handles spatial derivatives.

All the geometrical information is encapsulated inside the kernel. So the derivative operator $\vec \nabla$ has no effect on other quantities, which are considered spatially constant. Since the $\vec \nabla$ operator applied to $\Phi_{\alpha,x_j}$ gives  $$\vec\nabla\Phi_{\alpha,x_j}(x)=(d_r\phi)(||\vec x-\vec x_j||/\alpha) \vec\nabla||\vec x-\vec x_j||/\alpha.$$
which yields
 $$\vec\nabla W_{\alpha,x_j}=\frac{1}{\alpha^4\int_{0}^{+\infty}4\pi r ^2\phi(r)dr}(d_r\phi)(||\vec x-\vec x_j||/\alpha) \frac{\vec x-\vec x_j}{||\vec x-\vec x_j||}.$$
 
 While it is clear mathematically that $\vec\nabla W_{\alpha,x_j}(x_j)=0$, this can create numerical issues. So we need to set this gradient to $0$ when we can.

In [ ]:
def compute_gradient(particles):
    global alpha
    grad=np.zeros((len(particles),len(particles),3))
    for i in range (len(particles)):
        for j in range (len(particles)):
            r=particles[i].x-particles[j].x
            r_val=(r[0]**2+r[1]**2+r[2]**2)**.5
            if (r_val>0):
                r/=r_val
                grad[i,j]=dW(r_val,alpha)*r
    return grad            

We are now left with the mysterious $\vec f$ force density. To keep things simple we will look at a [toy star](https://doi.org/10.1111/j.1365-2966.2004.07748.x).  We take here the force density $\vec f$ to derive from a potential of the form $$U=G\sum_i\sum_jm_im_j||\vec x_i-\vec x_j||$$where $G$ is the gravitational constant.

We can now derive the trajectory of each meta-particle $i$ using the equation $$\frac{\text d\vec v_i}{\text dt}=-\frac{1}{\rho_i}\vec \nabla P+G \sum_j\rho_j(\vec x_j-\vec x_i)$$

This equation combines both the particle nature found in PIC code and the continuum mechanics nature (examplified by $P$) found inside this chapter. 

If we suppose that pressure equilibrates faster than particles can move (quasi-static transformations anyone??) we can [write](https://doi.org/10.1111/j.1365-2966.2004.07346.x) $$\frac{1}{\rho_i}\vec \nabla P=\sum_{j\ne i}m_j\Big(\frac{P_i}{\rho_i^2}+\frac{P_j}{\rho_j^2}\Big)\vec\nabla W_{\alpha}(\vec x_j-\vec x_i)$$

Putting it all together we get
$$\frac{\text d\vec v_i}{\text dt}=-\sum_jm_j\Big(\frac{P_i}{\rho_i^2}+\frac{P_j}{\rho_j^2}\Big)\vec\nabla W_{\alpha}(\vec x_j-\vec x_i)+G \sum_j\rho_j(\vec x_j-\vec x_i)$$

In [ ]:
def time_advance(particles,grad,dt=1,x_adv=1):
    global G,nu
    for i in range (len(particles)):
        for j in range(len(particles)):
            val=(particles[j].m*(particles[i].P/particles[i].rho**2+particles[j].P/particles[j].rho**2))*grad[j,i]
            val+=G*particles[j].rho*(particles[j].x-particles[i].x)
            particles[i].v+=val*dt/2.
        particles[i].v-=nu*particles[i].v*dt/2.
    if (x_adv==1):
        for i in range (len(particles)):
            particles[i].x+=particles[i].v*dt

In [ ]:
def recenter(particles):
    x_ave=np.zeros(3)
    m=0
    for i in range (len(particles)):
        x_ave+=particles[i].x
        m+=particles[i].m
    x_ave/=m
    for i in range (len(particles)):
        particles[i].x-=x_ave

In [ ]:
def get_min_dt(particles):
    global length
    dt_min=1e10
    for i in range (len(particles)):
        vel=(particles[i].v[0]**2+particles[i].v[1]**2+particles[i].v[2]**2)**.5+1e-3
        dt=length/vel/100
        if (dt_min>dt):
            dt_min=dt
    return dt

In [ ]:
def plot_3D(particles,plot_size=3,plot_axes=True,title=''):
    from mpl_toolkits.mplot3d import Axes3D
    n = len(particles)
    #coordinates
    data_x=np.zeros(n)
    data_y=np.zeros(n)
    data_z=np.zeros(n)
    data_m=np.zeros(n)
    for i in range(n):
        data_x[i]=cp[i].x[0]
        data_y[i]=cp[i].x[1]
        data_z[i]=cp[i].x[2]
        data_m[i]=cp[i].m
    #generate figure and axes
    fig = plt.figure(figsize=(plot_size,plot_size))
    ax = fig.add_subplot(111, projection='3d')
    ax.scatter(data_x, data_y, data_z, c=data_m, linewidths=0,
               marker='o', s=8*plot_size, cmap=plt.cm.Wistia,alpha=.8) #s is the size of the plotted symbol 'o'
    #set autoscale parameters
    xc=(data_x.max()+data_x.min())/2.
    x_low=xc-(data_x.max()-data_x.min())/2.*1.1-1e-12
    x_high=xc+(data_x.max()-data_x.min())/2.*1.1+1e-12
    yc=(data_y.max()+data_y.min())/2.
    y_low=yc-(data_y.max()-data_y.min())/2.*1.1-1e-12
    y_high=yc+(data_y.max()-data_y.min())/2.*1.1+1e-12
    zc=(data_z.max()+data_z.min())/2.
    z_low=zc-(data_z.max()-data_z.min())/2.*1.1-1e-12
    z_high=zc+(data_z.max()-data_z.min())/2.*1.1+1e-12
    #set autoscale parameters
    ax.set_xlim(min(x_low,y_low,z_low),max(x_high,y_high,z_high))
    ax.set_ylim(min(x_low,y_low,z_low),max(x_high,y_high,z_high))
    ax.set_zlim(min(x_low,y_low,z_low),max(x_high,y_high,z_high))
    ax.set_box_aspect((1,1,1))
    if (plot_axes):#so we can switch the axis on or off
        ax.set_xlabel("x (m)")
        ax.set_ylabel("y (m)")
        ax.set_zlabel("z (m)")
        ax.grid(False) 
        ax.w_xaxis.pane.fill = False
        ax.w_yaxis.pane.fill = False
        ax.w_zaxis.pane.fill = False
    else:
        ax.set_axis_off()
    fig.set_facecolor('black')
    ax.set_facecolor('black')
    plt.suptitle(title)
    plt.show()


In [ ]:
def plot_2D(particles):
    global length
    fig=plt.figure(figsize=(20,10))
    ax=fig.add_subplot(1,2,1)
    ax.set(xlim=(-length/2,length/2),ylim=(-length/2,length/2))
    n=len(particles)
    data_x=np.zeros(n)
    data_y=np.zeros(n)
    data_z=np.zeros(n)
    data_m=np.zeros(n)
    for i in range(n):
        data_x[i]=particles[i].x[0]
        data_y[i]=particles[i].x[1]
        data_z[i]=particles[i].x[2]
        data_m[i]=particles[i].m
    ax.scatter(data_x,data_y,c=data_m, cmap=plt.cm.Wistia, s=40, alpha=0.75)
    ax.set_facecolor('black')
    ax.set_xlabel("x")
    ax.set_ylabel("y")
    ax.set_box_aspect(1)
    ax=fig.add_subplot(1,2,2)
    ax.set(xlim=(-length/2,length/2),ylim=(-length/2,length/2))
    ax.scatter(data_x,data_z,c=data_m, cmap=plt.cm.Wistia, s=40, alpha=0.75)
    ax.set_xlabel("x")
    ax.set_ylabel("z")
    ax.set_box_aspect(1)
    ax.set_facecolor('black')
    clear_output(wait=True)
    show_inline_matplotlib_plots()


In [ ]:
ti=0
tf=2e-2
t=0
dt=3e-4
M=50
n_out=100
t_out=(tf-ti)/n_out
t_print=0
length=1
G=3.014
K=200
nu=300
alpha=.2

In [ ]:
domain=np.array([-length,length,-length,length,-length,length])
box=domain*.85
cp=np.empty(0,dtype=object)
N_total=100000
Nc=200 # the number of particle clumps (also called particles herein)
Np=max(int(N_total/Nc),1) # the number of particels per clump
M1=0
for i in range (Nc):
    cp=np.append(cp,particle()) # we load the protons
    cp[i].x=np.zeros(3)
    cp[i].v=np.zeros(3)
    r=length*np.random.random_sample()/2.
    theta=np.pi*np.random.random_sample()
    phi=2*np.pi*np.random.random_sample()
    cp[i].x[0]=r*np.cos(phi)*np.sin(theta)
    cp[i].x[1]=r*np.sin(phi)*np.sin(theta)
    cp[i].x[2]=r*np.cos(theta)
    cp[i].m=1
#     if (i>=Nc-1):
#         cp[i].m*=50
    M1+=cp[i].m
print(M1)
for i in range (Nc):
    cp[i].m*=M/M1

In [ ]:
from matplotlib import interactive
interactive(False)
%matplotlib inline
t=0
while (t<tf):
    compute_rho(cp)
    compute_pressure(cp,K=K)
    grad=compute_gradient(cp)
    time_advance(cp,grad,dt=dt)
    compute_rho(cp)
    compute_pressure(cp,K=K)
    grad=compute_gradient(cp)
    time_advance(cp,grad,dt=dt,x_adv=0)
    t+=dt
    t_print+=dt
    if (t_print>t_out):
#         recenter(cp)
        plot_2D(cp)
        t_print=0


In [ ]:
interactive(True)
%matplotlib qt
plot_3D(cp,plot_size=15,plot_axes=True,title='time '+str(t))


© Pierre Gourdain, The University of Rochester, Charlie Seyler, Cornell University, 2022
<br>Distributed under the license GNU GPLv3<br>
Sponsored by the NSF grants PHY-1943939 and PHY-2020249